In [46]:
import pandas as pd
from cleantext import clean
import re
import torch.nn.functional as F
import numpy as np

import torch
from torch import Tensor
from transformers import AutoTokenizer, AutoModel
from pandas import read_excel, read_json
import sys
import time
import math

In [2]:
dataset_path = "../datasets/"

In [3]:
reqres = pd.read_json(dataset_path + "Requêtes et résultats attendus.json")

In [4]:
reqres

question  \
0   Je suis tombé malade pendant mes congés, est-c...   
1   J’ai été en arrêt de travail pendant 45 jours,...   
2   J’ai quitté mon entreprise il y a 7 jours et j...   
3           Quel est mon salaire pendant mes congés ?   
4   Je suis licencié pour des raisons économiques,...   
5   Comment calculer l’ancienneté dans l’entrepris...   
6   A combien de jours de congés payés ai-je le dr...   
7   Si je démissionne et que je suis enceinte est-...   
8   Ai-je le droit à une indemnité si je suis décl...   
9   J'ai 62 ans. Mon employeur peut-il m'imposer d...   
10            Quelle est la durée maximale d'un CDD ?   
11  Un contrat écrit est-il obligatoire pour un CDD ?   
12          Combien de jours de congés pour mariage ?   
13  Combien de jours de congés pour le décès d’un ...   
14  A combien de jours de congés ai-je le droit po...   
15  A combien de jours de congés ai-je le droit po...   
16  Quelle est la durée du préavis en cas de démis...   
17  Quelle est la durée du préavis à respecter en ...   
18            Combien de préavis pour une démission ?   
19  Quelles sont les règles du maintien de salaire...   
20  Comment toucher 100 % de son salaire en arrêt ...   
21  Combien de temps dure le maintien de salaire e...   
22       Quel est le salaire en cas d’arrêt maladie ?   
23           Complément du salaire en arrêt maladie ?   
24  Est-il obligatoire d'avoir un contrat de trava...   
25  Est-ce que je peux travailler sans avoir signé...   
26       Puis-je travailler sans contrat de travail ?   
27  Est-ce que je peux travailler si mon contrat d...   
28  Est-ce que le contrat de travail est obligatoi...   
29       La prime d’ancienneté est-elle obligatoire ?   
30     Quel est le montant de la prime d’ancienneté ?   
31       La prime d’ancienneté est elle obligatoire ?   
32  A partir de quand peut-on avoir la prime d’anc...   
33  Qui a le droit à la prime de départ à la retra...   
34  Quel est le montant de la prime de départ à la...   
35  Est-ce que la prime de départ à la retraite es...   
36  Comment calculer la prime de départ à la retra...   
37  Montant de l’indemnité de départ à la retraite...   
38  Quel est le délai pour avertir son employeur d...   
39  Combien de temps pour prévenir son employeur d...   
40    Comment calculer la prime médaille du travail ?   
41  Quel est le montant de la prime pour la médail...   
42  Quelles sont les conséquences du non-respect d...   
43                Comment démissionner sans préavis ?   
44  Que risque un salarié qui ne fait pas son préa...   
45  Que se passe-t-il si on ne fait pas son préavis ?   
46  Que faire si un salarié ne respecte pas son pr...   
47  Comment calculer la majoration pour le travail...   
48  Quelle est la majoration quand on travaille le...   
49  Quel est le salaire quand on travaille le dima...   
50  Quel est le taux horaire quand on travaille le...   
51  Je fais de l'insertion. Est-ce que je peux uti...   
52  Je travaille mais mon employeur ne m'a pas déc...   
53  Je m'occupe de mon enfant malade. Je peux avoi...   
54  Je suis travailleur handicapé. Qu'est-ce-que ç...   
55                                                      

                                      expectedResults  
0   [{'slug': 'contribution/si-le-salarie-est-mala...  
1   [{'slug': 'information/suivi-medical-et-accomp...  
2   [{'slug': 'modeles-de-courriers/lettre-de-recl...  
3   [{'slug': 'fiche-service-public/comment-est-ca...  
4   [{'slug': 'fiche-service-public/licenciement-e...  
5   [{'slug': 'fiche-service-public/comment-calcul...  
6   [{'slug': 'fiche-service-public/conges-payes',...  
7   [{'slug': 'fiche-service-public/une-salariee-p...  
8   [{'slug': 'fiche-service-public/le-salarie-tou...  
9   [{'slug': 'fiche-service-public/un-employeur-p...  
10  [{'slug': 'contribution/quelle-peut-etre-la-du...  
11  [{'slug': 'fiche-service-public/le-contrat-de-...  
12  [{'slug': 'contribution/les-conges-pour-evenem...  
13  [{'slug

In [5]:
device =  'cuda:0' if torch.cuda.is_available() else 'cpu'
device

'cuda:0'

In [6]:
window_size = 310
slide = 70

In [7]:
def make_windows(content, w_size, slide):
    if slide > w_size :
        raise Exception()
    tokens = content.split(" ")
    l = len(tokens)    
       
    n = math.ceil(l / (w_size-slide))        

    if n==1 :
        return [content]
    else :
        windows = []
        for i in range(n) :            
            x = i*slide
            if x < l :
                y = x + w_size
                w = tokens[x:y]
                windows.append(" ".join(w))
        
        return windows

In [8]:
fiches = pd.read_csv(dataset_path + "xp-documents-fiches (2).csv")

In [9]:
fiches["cleaned_text"] = fiches["text"].apply(lambda t : clean(re.sub("\s+", " ", str(t)), to_ascii=False))
fiches["tokens"] = fiches["cleaned_text"].apply(lambda t : len(str(t).split(" ")))

In [10]:
fiches = fiches[fiches["tokens"]<3000]

In [11]:
fiches["windows"] = fiches["cleaned_text"].apply(lambda t : make_windows(t, window_size, slide))
fiches.drop(columns=["cleaned_text", "text"], inplace=True)
fiches = fiches.explode("windows", ignore_index=True)
fiches.rename(columns={"windows": "text"}, inplace=True)

In [12]:
fiches["cdtnId-fiches"] = fiches["cdtnId"]
fiches["cdtnId"] = fiches["cdtnId"].apply(lambda x : x.split("-")[0])

In [13]:
contribs = pd.read_csv(dataset_path + "xp-documents-contribs (1).csv")

In [14]:
contribs.drop_duplicates(subset=["answers.generic.text"], inplace=True)
contribs["cleaned_text"] = contribs["answers.generic.text"].apply(lambda t : clean(re.sub("\s+", " ", str(t)), to_ascii=False))
contribs["tokens"] = contribs["cleaned_text"].apply(lambda t : len(str(t).split(" ")))
contribs["windows"] = contribs["cleaned_text"].apply(lambda t : make_windows(t, window_size, slide))
contribs.drop(columns=["cleaned_text","answers.generic.text","text"], inplace=True)
contribs = contribs.explode("windows", ignore_index=True)
contribs.rename(columns={"windows": "text"}, inplace=True)

In [15]:
contribs["slug"] = contribs["slug"].apply(lambda s: "-".join(s.split("-")[1:]))

In [16]:
contribs_tensor = torch.load(dataset_path + 'contribs_tensor3.pt')
fiches_tensor = torch.load(dataset_path + 'fiches_tensor3.pt')

#contribs_tensor = torch.load(dataset_path + 'contribs_tensor4.pt')
#fiches_tensor = torch.load(dataset_path + 'fiches_tensor4.pt')
tensor_docs = torch.vstack([fiches_tensor, contribs_tensor]).to(device)

In [17]:
passages_set = pd.concat([fiches, contribs]).reset_index()
passages_set.shape

(4795, 9)

In [18]:
def average_pool(last_hidden_states: Tensor,
                 attention_mask: Tensor) -> Tensor:
    last_hidden = last_hidden_states.masked_fill(~attention_mask[..., None].bool(), 0.0)
    return last_hidden.sum(dim=1) / attention_mask.sum(dim=1)[..., None]

tokenizer = AutoTokenizer.from_pretrained('intfloat/multilingual-e5-base')
model = AutoModel.from_pretrained('intfloat/multilingual-e5-base').to(device)

In [19]:
query = "j'ai été en arrêt de travail pendant 45 jours, dois-je faire une visite médicale avant de reprendre ?"
# embbed query
batch_dict = tokenizer('query: '+ query, max_length=512, padding=True, truncation=True, return_tensors='pt').to(device)

outputs = model(**batch_dict)
embeddings = average_pool(outputs.last_hidden_state, batch_dict['attention_mask']).detach()
question_normalized_embeddings = F.normalize(embeddings, p=2, dim=1)

# score against all passages and retrieve top k

retrieval_scores = (question_normalized_embeddings @ tensor_docs.T)[0] * 100

pd_k = 50
rr_k = 11
    
j = torch.argmax(retrieval_scores).item()
topk = torch.topk(retrieval_scores, pd_k)
matches = topk.values.tolist()
matching_indices = topk.indices.tolist()
#print(matches)
#print(matching_indices)



In [20]:

# reranker
batch = ['query: '+ query]

for m in matching_indices[:rr_k] :
    batch.append('passage: ' + passages_set.loc[m]["text"])

print(len(batch))
batch   


12


["query: j'ai été en arrêt de travail pendant 45 jours, dois-je faire une visite médicale avant de reprendre ?",
 "passage: vous vous demandez comment votre reprise du travail va s'effectuer à la suite de votre arrêt maladie ? vous souhaitez savoir si vous allez être soumis ou non à une visite médicale, si le médecin du travail va vous permettre de bénéficier d'un aménagement de votre poste de travail, d'une adaptation de votre temps de travail pour raison thérapeutique, d'un reclassement ? les informations diffèrent selon la durée de votre arrêt maladie. nous vous communiquons les éléments à connaître. attention : cette fiche ne présente que le cas d'un arrêt maladie ayant débuté à compter du 1 er avril 2022 . arrêt de moins de 60 jours qu'est-ce que le rendez-vous de liaison ? pour les arrêts de plus de 30 jours , un rendez-vous de liaison peut être mis en place entre le salarié et l'employeur en faisant participer le service de prévention et de santé au travail. cet entretien a pour

In [21]:
batch_dict = tokenizer(batch, max_length=512, padding=True, truncation=True, return_tensors='pt').to(device)
batch_dict.input_ids.size()

torch.Size([12, 477])

In [22]:
with torch.no_grad():
    outputs = model(**batch_dict)


In [ ]:

outputs = model(**batch_dict)
embeddings = average_pool(outputs.last_hidden_state, batch_dict['attention_mask']).detach()
normalized_embeddings = F.normalize(embeddings, p=2, dim=1)

reranker_scores = (normalized_embeddings[0] @ normalized_embeddings[1:].T) * 100
print(reranker_scores)
    
#print(reranker_scores)
rr_matches = torch.topk(reranker_scores, rr_k).values.tolist()
rr_matching_indices = torch.topk(reranker_scores, rr_k).indices.tolist()
#print(len(rr_matching_indices))
#print(rr_matching_indices)

final_indices = [matching_indices[m] for m in rr_matching_indices]
#print(final_indices)

#print(query)

In [30]:
def search(query, verbose=False):
    with torch.no_grad():

        # embbed query
        batch_dict = tokenizer('query: '+ query, max_length=512, padding=True, truncation=True, return_tensors='pt').to(device)
    
        outputs = model(**batch_dict)
        embeddings = average_pool(outputs.last_hidden_state, batch_dict['attention_mask']).detach()
        question_normalized_embeddings = F.normalize(embeddings, p=2, dim=1)
    
        # score against all passages and retrieve top k
        
        retrieval_scores = (question_normalized_embeddings @ tensor_docs.T)[0] * 100
        
        pd_k = 100
        rr_k = 70
            
        j = torch.argmax(retrieval_scores).item()
        topk = torch.topk(retrieval_scores, pd_k)
        matches = topk.values.tolist()
        matching_indices = topk.indices.tolist()
        #print(matches)
        #print(matching_indices)
    
        # reranker
        batch = ['query: '+ query]
    
        for m in matching_indices[:rr_k] :
            batch.append('passage: ' + passages_set.loc[m]["text"])
        
        #print(len(batch))
            
        batch_dict = tokenizer(batch, max_length=512, padding=True, truncation=True, return_tensors='pt').to(device)
    
        outputs = model(**batch_dict)
        embeddings = average_pool(outputs.last_hidden_state, batch_dict['attention_mask']).detach()
        normalized_embeddings = F.normalize(embeddings, p=2, dim=1)

        reranker_scores = (normalized_embeddings[0] @ normalized_embeddings[1:].T) * 100
        #print(reranker_scores)
            
        #print(reranker_scores)
        rr_matches = torch.topk(reranker_scores, rr_k).values.tolist()
        rr_matching_indices = torch.topk(reranker_scores, rr_k).indices.tolist()
        #print(len(rr_matching_indices))
        #print(rr_matching_indices)
    
        final_indices = [matching_indices[m] for m in rr_matching_indices]
        #print(final_indices)
        
        #print(query)
    
        res = passages_set.loc[final_indices][["index","source","cdtnId","title","text", "tokens", "slug"]]
        
        # res = res.head(7)
    
        if verbose:
            display(res[["source", "cdtnId", "slug", "title", "text"]].style.set_properties(**{
                'text-align': 'left',
                'white-space': 'pre-wrap',
            }))
    
        return {"dot_prod": matching_indices, "reranked": final_indices}

In [167]:
indices = search("j'ai été en arrêt de travail pendant 45 jours, dois-je faire une visite médicale avant de reprendre ?", True)

In [46]:
i = 21
q = reqres.loc[i].question
exp = reqres.loc[i].expectedResults

print(q)
indices = search(q)

Combien de temps dure le maintien de salaire en arrêt maladie ?


In [48]:
exp

[{'slug': 'contribution/en-cas-darret-maladie-du-salarie-lemployeur-doit-il-assurer-le-maintien-de-salaire',
  'cdtnId': '90c0113ee8',
  'exists': True,
  'dp_pos': 2,
  'rr_pos': 2},
 {'slug': 'fiche-service-public/arret-maladie-indemnites-journalieres-versees-au-salarie',
  'cdtnId': 'c988c4309a',
  'exists': True,
  'dp_pos': -1,
  'rr_pos': -1},
 {'slug': 'fiche-service-public/accident-du-travail-indemnites-journalieres-pendant-larret-de-travail',
  'cdtnId': '81827a4518',
  'exists': True,
  'dp_pos': -1,
  'rr_pos': -1},
 {'slug': 'fiche-service-public/maladie-professionnelle-indemnites-journalieres-pendant-larret-de-travail',
  'cdtnId': 'f358ba9e16',
  'exists': True,
  'dp_pos': -1,
  'rr_pos': -1}]

In [49]:
rr_res = passages_set.loc[indices["reranked"]][["index","source", "slug", "cdtnId","title","text", "tokens"]]
rr_res

index                    source  \
1047   1047  fiches_ministere_travail   
3184   3184     fiches_service_public   
4785     57             contributions   
3093   3093     fiches_service_public   
4079   4079     fiches_service_public   
3094   3094     fiches_service_public   
1004   1004  fiches_ministere_travail   
4354   4354     fiches_service_public   
2920   2920     fiches_service_public   
934     934  fiches_ministere_travail   

                                                   slug      cdtnId  \
1047  protection-sociale-des-demandeurs-demploi#Quel...  5d951a2ab0   
3184  un-salarie-peut-il-revenir-travailler-avant-la...  4080afb815   
4785  en-cas-darret-maladie-du-salarie-lemployeur-do...  15928e276c   
3093  arret-maladie-pendant-le-preavis-quelles-conse...  36c2fc8868   
4079  un-salarie-en-arret-de-travail-peut-il-suivre-...  ada1458994   
3094  arret-maladie-pendant-le-preavis-quelles-conse...  36c2fc8868   
1004  lindemnisation-legale-des-absences-pour-maladi...  5a1ef115ab   
4354  un-salarie-peut-il-garder-la-complementaire-sa...  cfecd65985   
2920  salarie-en-arret-maladie-pendant-un-conge-pare...  282a0f7055   
934   5-questions-reponses-sur-la-sante-au-travail#t...  55a26a9073   

                                                  title  \
1047  Protection sociale des demandeurs d’emploi : q...   
3184  Un salarié peut-il revenir travailler avant la...   
4785  En cas d’arrêt maladie du salarié, l’employeur...   
3093  Arrêt maladie pendant le préavis : quelles con...   
4079  Un salarié en arrêt de travail peut-il suivre ...   
3094  Arrêt maladie pendant le préavis : quelles con...   
1004  L’indemnisation légale des absences pour malad...   
4354  Un salarié peut-il garder la complémentaire sa...   
2920  Salarié en arrêt maladie pendant un congé pare...   
934   La santé au travail : médecine du travail : qu...   

                                                   text  tokens  
1047  le de est assuré socialil bénéficie du maintie...     165  
3184  auprès du médecin du travail est obligatoire d...     288  
4785  le code du travail prévoit des conditions du m...     848  
3093  quelle conséquence sur la rémunération ? vous ...     420  
4079  primaire d'assurance maladie (cpam) participe....     274  
3094  de l'accident. maladie non professionnelle l'a...     420  
1004  en cas d'accident du travail ou de maladie pro...     156  
4354  l'organisme assureur de la cessation du versem...    1269  
2920  de frais de santé pour maladie pendant toute l...     275  
934   le code du travail fixe à 5 ans le délai maxim...     146

In [141]:
def process(e, verbose = False) :
    q = e.question
    exp = e.expectedResults

    #print(i)
    print(q)
    indices = search(q)
    
    
    dp_res = passages_set.loc[indices["dot_prod"]][["index","source", "slug", "cdtnId","title","text", "tokens"]].reset_index()
    # if verbose:
    #     display(dp_res[["source", "cdtnId", "slug", "title", "text"]].style.set_properties(**{
    #         'text-align': 'left',
    #         'white-space': 'pre-wrap',
    #     }))
    
    rr_res = passages_set.loc[indices["reranked"]][["index","source", "slug", "cdtnId","title","text", "tokens"]].reset_index()
    if verbose:
        display(rr_res[["source", "cdtnId", "slug", "title", "text"]].style.set_properties(**{
            'text-align': 'left',
            'white-space': 'pre-wrap',
        }))

    dp_res.drop_duplicates(subset=['cdtnId'], inplace=True)
    rr_res.drop_duplicates(subset=['cdtnId'], inplace=True)
    
    for e in exp :
        cdtnId = e["cdtnId"]    
        slug = e["slug"].split("/")[1]
        
        found = passages_set[passages_set["cdtnId"] == cdtnId].shape[0] > 0
    
        if not found :        
            found = passages_set[passages_set["slug"] == slug].shape[0] > 0

        if not found :
             e["dp_pos"] = np.NaN
             e["rr_pos"] = np.NaN

        e["exists"] = found
    
        if found :
            dp_pos = dp_res[dp_res["cdtnId"] == cdtnId]
            if dp_pos.shape[0] < 1 :
                dp_pos = dp_res[dp_res["slug"] == slug]
            if dp_pos.shape[0] > 0 :
                e["dp_pos"] = dp_pos.index[0]
            else :
                e["dp_pos"] = np.NaN
    
            rr_pos = rr_res[rr_res["cdtnId"] == cdtnId]
            if rr_pos.shape[0] < 1 :
                rr_pos = rr_res[rr_res["slug"] == slug]
            if rr_pos.shape[0] > 0 :
                e["rr_pos"] = rr_pos.index[0]
            else :
                e["rr_pos"] = np.NaN
    df = pd.json_normalize(exp)
    display(df[["slug","cdtnId","exists","dp_pos","rr_pos"]].style.set_properties(**{
        'text-align': 'left',
        'white-space': 'pre-wrap',
    }))
    
    return df


In [142]:
def evaluate(q, r):
    # number and percentage of available results (exists)
    existing = r[r["exists"]]
    n = existing.shape[0]
    n_ratio = n / r.shape[0]
    # for existing, % of matches
    dp = existing[existing["dp_pos"] >= 0]
    if n>0 :
        match_ratio = dp.shape[0] / n
    else :
        match_ratio = 0
        
    if match_ratio >= 0 and dp["dp_pos"].sum() :
        # mean rank for dp / rr
        # sum of dp / rr
        dp_sum = dp["dp_pos"].sum()
        dp_mean = dp_sum / dp.shape[0] 
    
        rr = existing[existing["rr_pos"] >= 0]
        rr_sum = rr["rr_pos"].sum()
        rr_mean = rr_sum / rr.shape[0]
    else : 
        dp_sum = np.NaN
        dp_mean = np.NaN
        rr_sum = np.NaN
        rr_mean = np.NaN
    
    return {"query": q, "exists":n, "exists_ratio":n_ratio, "match_ratio":match_ratio, "dp_sum":dp_sum, "dp_mean":dp_mean, "rr_sum":rr_sum, "rr_mean":rr_mean}


In [172]:
i = 7
rr = reqres.iloc[i]
r = process(rr)

evaluate(rr.question, r)

Si je démissionne et que je suis enceinte est-ce que j’ai un préavis ?


{'query': 'Si je démissionne et que je suis enceinte est-ce que j’ai un préavis ?',
 'exists': 2,
 'exists_ratio': 1.0,
 'match_ratio': 1.0,
 'dp_sum': 8,
 'dp_mean': 4.0,
 'rr_sum': 8,
 'rr_mean': 4.0}

In [132]:
results = []
for i in range(len(reqres) - 1) :   
    print(i)
    results.append(process(reqres.iloc[i]))
    print("\n")


evaluations = []
for req, r in zip(reqres.values.tolist(), results):
    # display(r[["slug","cdtnId","exists","dp_pos","rr_pos"]].style.set_properties(**{
    #     'text-align': 'left',
    #     'white-space': 'pre-wrap',
    # }))
    evaluations.append(evaluate(req[0], r))



0
Je suis tombé malade pendant mes congés, est-ce que mes congés peuvent être repoussés ?




1
J’ai été en arrêt de travail pendant 45 jours, dois-je faire une visite médicale avant de reprendre ?




2
J’ai quitté mon entreprise il y a 7 jours et je n’ai toujours pas eu de certificat de travail, que dois-je faire ?




3
Quel est mon salaire pendant mes congés ?




4
Je suis licencié pour des raisons économiques, quel est le montant de l’indemnité ?


...



50
Quel est le taux horaire quand on travaille le dimanche




51
Je fais de l'insertion. Est-ce que je peux utiliser un chèque emploi ?




52
Je travaille mais mon employeur ne m'a pas déclaré. Je fais quoi ?




53
Je m'occupe de mon enfant malade. Je peux avoir une avance sur l'allocation ?




54
Je suis travailleur handicapé. Qu'est-ce-que ça veut dire pour ma retraite ?


In [144]:
formatters = {
    'dp_mean': '{:,.2f}'.format,
    'rr_mean': '{:,.2f}'.format,
    'match_ratio': '{:,.2f}'.format,
    'exists_ratio': '{:,.2%}'.format,
    'match_ratio': '{:,.2%}'.format
}

print(pd.json_normalize(evaluations).sort_values(['rr_sum']).to_string(formatters=formatters))


                                                                                                                 query  exists exists_ratio match_ratio  dp_sum dp_mean  rr_sum rr_mean
44                                                                 Que risque un salarié qui ne fait pas son préavis ?       1      100.00%     100.00%     2.0    2.00     0.0    0.00
53                                       Je m'occupe de mon enfant malade. Je peux avoir une avance sur l'allocation ?       1      100.00%     100.00%     1.0    1.00     0.0    0.00
2   J’ai quitté mon entreprise il y a 7 jours et je n’ai toujours pas eu de certificat de travail, que dois-je faire ?       1       50.00%     100.00%     1.0    1.00     0.0    0.00
28                                      Est-ce que le contrat de travail est obligatoire pour commencer à travailler ?       5      100.00%      20.00%     1.0    1.00     0.0    0.00
46                                                                 Que faire si 

In [145]:
pd.json_normalize(evaluations).describe()

exists  exists_ratio  match_ratio     dp_sum    dp_mean     rr_sum  \
count  55.000000     55.000000    55.000000  41.000000  41.000000  41.000000   
mean    1.963636      0.880303     0.838485  22.341463  11.786585  14.560976   
std     1.332828      0.250393     0.333023  24.655232  13.619992  17.163987   
min     0.000000      0.000000     0.000000   1.000000   0.500000   0.000000   
25%     1.000000      1.000000     1.000000   3.000000   2.000000   1.000000   
50%     2.000000      1.000000     1.000000   8.000000   5.750000   8.000000   
75%     2.000000      1.000000     1.000000  35.000000  17.000000  24.000000   
max     5.000000      1.000000     1.000000  90.000000  53.000000  74.000000   

         rr_mean  
count  41.000000  
mean    7.623984  
std     9.228807  
min     0.000000  
25%     1.000000  
50%     4.000000  
75%    12.000000  
max    38.000000

In [136]:
print(results[19].to_string())

                                                                                              slug      cdtnId  exists  dp_pos  rr_pos
0  contribution/en-cas-darret-maladie-du-salarie-lemployeur-doit-il-assurer-le-maintien-de-salaire  90c0113ee8    True       7       1


In [147]:
resp = search("enfant")
rr_res = passages_set.loc[resp["reranked"]][["index","source", "slug", "cdtnId","title","text", "tokens"]].reset_index()
display(rr_res[["source", "cdtnId", "slug", "title", "text"]].style.set_properties(**{
    'text-align': 'left',
    'white-space': 'pre-wrap',
}))

In [68]:
pq = pd.read_csv(dataset_path + "xp-documents-prequalified.csv")

In [98]:
def toArray(flat):
    return flat.split(", ")
    
def parsePQ(row) :
    questions = toArray(row["variants"]) 
    cdtnIds = toArray(row["refs.cdtnId"])
    slugs = toArray(row["refs.slug"])
    sources = toArray(row["refs.source"])
    expectedResults = []
    for [id, slug, source] in zip(cdtnIds, slugs, sources) :
        if source != "code_du_travail":
            expectedResults.append({"cdtnId" : id, "slug": source+"/"+slug, "source":source})
    pqs = [{"question": question, "expectedResults": expectedResults} for question in questions[:3]]
    #print(pqs)
    return pqs

pqDF = pq.apply(lambda row: parsePQ(row), axis=1).explode()
pqPrepro = pd.json_normalize(pqDF)
pqPrepro

question  \
0                       rupture conventionnelle-refus   
1                    refus de rupture conventionnelle   
2                       refus rupture conventionnelle   
3                                                dpae   
4                  déclaration préalable à l'embauche   
..                                                ...   
903           indemnité de licenciement et inaptitude   
904  Est-ce que je peux être licencié pour inaptitude   
905                    complement salaire pole emploi   
906                 complement de salaire pole emploi   
907                 complément de salaire pole emploi   

                                       expectedResults  
0    [{'cdtnId': '36a5eef9e4', 'slug': 'fiches_serv...  
1    [{'cdtnId': '36a5eef9e4', 'slug': 'fiches_serv...  
2    [{'cdtnId': '36a5eef9e4', 'slug': 'fiches_serv...  
3    [{'cdtnId': '799dc7e99a', 'slug': 'page_fiche_...  
4    [{'cdtnId': '799dc7e99a', 'slug': 'page_fiche_...  
..                                                 ...  
903  [{'cdtnId': '3fc2707973', 'slug': 'fiches_serv...  
904  [{'cdtnId': '3fc2707973', 'slug': 'fiches_serv...  
905  [{'cdtnId': '497e31d14c', 'slug': 'page_fiche_...  
906  [{'cdtnId': '497e31d14c', 'slug': 'page_fiche_...  
907  [{'cdtnId': '497e31d14c', 'slug': 'page_fiche_...  

[908 rows x 2 columns]

In [99]:
#pqPrepro[["expectedResults"]].loc[0][0]

In [149]:
dataset = pqPrepro
results_pq = []
for i in range(len(dataset) - 1) :      
    print(i)
    try :
        results_pq.append(process(dataset.iloc[i]))
    except:
        results_pq.append(None)
    print("\n")



0
rupture conventionnelle-refus




1
refus de rupture conventionnelle




2
refus rupture conventionnelle




3
dpae




4
déclaration préalable à l'embauche


...



902
procédure licenciement pour inaptitude




903
indemnité de licenciement et inaptitude




904
Est-ce que je peux être licencié pour inaptitude




905
complement salaire pole emploi




906
complement de salaire pole emploi


In [164]:

evaluations_pq = []
for req, r in zip(dataset.values.tolist(), results_pq):
    # display(r[["slug","cdtnId","exists","dp_pos","rr_pos"]].style.set_properties(**{
    #     'text-align': 'left',
    #     'white-space': 'pre-wrap',
    # }))
    #print(r)
    if r is None: 
        evaluations_pq.append(None)
    else :
        evaluations_pq.append(evaluate(req[0], r))

/tmp/ipykernel_16141/2133406217.py:21: RuntimeWarning: invalid value encountered in scalar divide
  rr_mean = rr_sum / rr.shape[0]


In [165]:
print(pd.json_normalize(evaluations_pq).sort_values(['rr_sum']).to_string(formatters=formatters))

                                                                                                                      query  exists exists_ratio match_ratio  dp_sum dp_mean  rr_sum rr_mean
387                                                                                                                   covid     2.0       40.00%      50.00%    78.0   78.00     0.0     NaN
125                                                                                   frais de deplacement domicile travail     2.0      100.00%      50.00%    77.0   77.00     0.0     NaN
124                                                                                      frais deplacement domicile travail     2.0      100.00%      50.00%    86.0   86.00     0.0     NaN
288                                                                                                        temps de-travail     7.0      100.00%      28.57%    85.0   42.50     0.0    0.00
797                                                    

In [166]:
pd.json_normalize(evaluations_pq).describe()

exists  exists_ratio  match_ratio      dp_sum     dp_mean  \
count  904.000000    904.000000   904.000000  782.000000  782.000000   
mean     3.567478      0.867503     0.749437   60.369565   19.962077   
std      2.318466      0.213820     0.311915   63.152866   17.675164   
min      0.000000      0.000000     0.000000    1.000000    0.500000   
25%      2.000000      0.750000     0.500000   13.000000    6.000000   
50%      3.000000      1.000000     0.857143   41.500000   15.916667   
75%      5.000000      1.000000     1.000000   91.750000   29.625000   
max     15.000000      1.000000     1.000000  484.000000   97.000000   

           rr_sum     rr_mean  
count  782.000000  767.000000  
mean    38.021739   12.786240  
std     44.816922   11.549563  
min      0.000000    0.000000  
25%      6.000000    3.583333  
50%     22.500000   10.000000  
75%     56.000000   18.833333  
max    381.000000   68.000000

In [158]:
type(None)

NoneType

In [83]:
dataset.values.tolist()[0]

['rupture conventionnelle-refus',
 [{'cdtnId': '36a5eef9e4',
   'slug': 'fiches_service_public/rupture-conventionnelle',
   'source': 'fiches_service_public',
   'exists': True,
   'dp_pos': 0,
   'rr_pos': 1},
  {'cdtnId': 'baf48a8630',
   'slug': 'page_fiche_ministere_travail/rupture-conventionnelle-collective',
   'source': 'page_fiche_ministere_travail',
   'exists': True,
   'dp_pos': 11,
   'rr_pos': 3}]]

                                                                                                query  exists exists_ratio match_ratio  dp_sum dp_mean  rr_sum rr_mean
312                                                        report du congé pour création d'entreprise       2      100.00%     100.00%    96.0   48.00     0.0    0.00
350  risque sérieux atteinte à la santé à la sécurité ou à intégrité physique ou morale de l'apprenti       3       75.00%      33.33%    83.0   83.00     0.0     NaN
311                                                             report du congé création d'entreprise       2      100.00%     100.00%    75.0   37.50     0.0    0.00
125                                                             frais de deplacement domicile travail       2      100.00%      50.00%    77.0   77.00     0.0     NaN
124                                                                frais deplacement domicile travail       2      100.00%      50.00%    86.0   86.00     0.0     Na